In [1]:
import pandas as pd
import numpy as np

from plotly.subplots import make_subplots
import plotly.graph_objects as go



In [26]:
metals = pd.read_csv("precious_metal_all.csv")

##### convert to date time data type
metals["date"] = pd.to_datetime(metals["date"])
metals["year"] = metals["date"].dt.year

##### fill NaN by average
metals["silver_troy_oz_usd"] = metals["silver_troy_oz_usd"].fillna(method="ffill")

##### convert troy ounce to gram -- 1 troy oz  = 31.1035 g
metals["gold_gram_usd"] = metals["gold_troy_oz_usd"]/31.1035
metals["silver_gram_usd"] = metals["silver_troy_oz_usd"]/31.1035

##### convert usd to myr
metals["gold_gram_myr"] = metals["gold_gram_usd"] * metals["usd_to_myr"]
metals["silver_gram_myr"] = metals["silver_gram_usd"] * metals["usd_to_myr"]



metals.loc[2940:2945,:]

date  usd_to_myr  gold_troy_oz_usd  silver_troy_oz_usd  year  \
2940 2023-01-19    4.308500       1931.869903            23.85000  2023   
2941 2023-01-20    4.286327       1926.409983            23.91900  2023   
2942 2023-01-21    4.285500       1926.409983            23.91900  2023   
2943 2023-01-22    4.286327       1926.409983            23.93850  2023   
2944 2023-01-23    4.285500       1931.465053            23.38000  2023   
2945 2023-01-24    4.285500       1936.979969            23.63585  2023   

      gold_gram_usd  silver_gram_usd  gold_gram_myr  silver_gram_myr  
2940      62.111013         0.766795     267.605301         3.303735  
2941      61.935473         0.769013     265.475666         3.296241  
2942      61.935473         0.769013     265.424469         3.295606  
2943      61.935473         0.769640     265.475666         3.298929  
2944      62.097997         0.751684     266.120967         3.221341  
2945      62.275306         0.759910     266.880822         3.256593

In [33]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace( go.Scatter(x=metals["date"], y=metals["gold_gram_myr"],
                          marker=dict(color="#8B0000")),
              row=1, col=1)
fig.add_trace( go.Scatter(x=metals["date"], y=metals["silver_gram_myr"],
                          marker=dict(color="#0047AB")),
              row=2, col=1)

fig.show()

----
----
# <center> Palm Oil </center>

---

In [27]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

from inflection import underscore
from tensorflow import keras
from keras.callbacks import EarlyStopping
from keras.models import Sequential
from keras.layers import Dense, LSTM, RepeatVector, TimeDistributed
from numpy.random import uniform
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
from statsmodels.tsa.stattools import acf
from statsmodels.tsa.seasonal import STL




In [2]:
palm = pd.read_csv("palm_oil.csv")
palm.columns = [underscore(val) for val in palm.columns]
palm = palm.rename(columns={"price":"close"})
palm["date"] = pd.to_datetime(palm["date"])
palm = palm.set_index(palm["date"])
palm = palm.asfreq(freq="d").drop(columns=["date"])

##### convert to float
palm["close"] = palm["close"].str.replace(",","").astype(float)
palm["open"] = palm["open"].str.replace(",","").astype(float)
palm["high"] = palm["high"].str.replace(",","").astype(float)
palm["low"] = palm["low"].str.replace(",","").astype(float)
palm["vol."] = palm["vol."].str.rstrip("K").astype(float)*1000
palm["change %"] = palm["change %"].str.rstrip("%").astype(float)

##### Add days name
palm["days"] = palm.index.day_name()

##### column to keep NaN record
palm["no_business"] = palm["close"].isna()

##### replace Nan values
palm["close"] = palm["close"].fillna(method="ffill")
palm["open"] = palm["open"].fillna(method="ffill")
palm["high"] = palm["high"].fillna(method="ffill")
palm["low"] = palm["low"].fillna(method="ffill")
palm["vol."] = palm["vol."].fillna(method="ffill")
palm["change %"] = palm["change %"].fillna(method="ffill")

palm = palm.reset_index()

palm

date   close    open    high     low    vol.  change %       days  \
0    2015-01-02  2315.0  2265.0  2325.0  2265.0  1600.0      1.05     Friday   
1    2015-01-03  2315.0  2265.0  2325.0  2265.0  1600.0      1.05   Saturday   
2    2015-01-04  2315.0  2265.0  2325.0  2265.0  1600.0      1.05     Sunday   
3    2015-01-05  2298.0  2303.0  2320.0  2293.0   270.0     -0.73     Monday   
4    2015-01-06  2309.0  2320.0  2333.0  2305.0   590.0      0.48    Tuesday   
...         ...     ...     ...     ...     ...     ...       ...        ...   
3279 2023-12-25  3677.0  3655.0  3679.0  3630.0   900.0      0.08     Monday   
3280 2023-12-26  3699.0  3683.0  3700.0  3675.0   880.0      0.60    Tuesday   
3281 2023-12-27  3700.0  3700.0  3722.0  3690.0  1250.0      0.03  Wednesday   
3282 2023-12-28  3657.0  3685.0  3695.0  3656.0  1560.0     -1.16   Thursday   
3283 2023-12-29  3662.0  3663.0  3675.0  3610.0   940.0      0.14     Friday   

      no_business  
0           False  
1            True  
2            True  
3           False  
4           False  
...           ...  
3279         True  
3280        False  
3281        False  
3282        False  
3283        False  

[3284 rows x 9 columns]

----
# <center> Data Analysis </center>

---

In [105]:
##### Make copy of palm data
palm_analysis = palm.copy(deep=True)
palm_analysis["mean_price"] = palm_analysis[["close", "open", "high", "low"]].mean(axis=1)
palm_analysis.head(5)

##### New columns
palm_analysis["high-low"] = palm_analysis["high"] - palm_analysis["low"]
palm_analysis["open-close"] = palm_analysis["open"] - palm_analysis["close"]

palm_analysis.head(5)

# palm_diff = palm_analysis.drop(columns=["days", "no_business"]).diff(1)
# palm_diff

date   close    open    high     low    vol.  change %      days  \
0 2015-01-02  2315.0  2265.0  2325.0  2265.0  1600.0      1.05    Friday   
1 2015-01-03  2315.0  2265.0  2325.0  2265.0  1600.0      1.05  Saturday   
2 2015-01-04  2315.0  2265.0  2325.0  2265.0  1600.0      1.05    Sunday   
3 2015-01-05  2298.0  2303.0  2320.0  2293.0   270.0     -0.73    Monday   
4 2015-01-06  2309.0  2320.0  2333.0  2305.0   590.0      0.48   Tuesday   

   no_business  mean_price  high-low  open-close  
0        False     2292.50      60.0       -50.0  
1         True     2292.50      60.0       -50.0  
2         True     2292.50      60.0       -50.0  
3        False     2303.50      27.0         5.0  
4        False     2316.75      28.0        11.0

In [25]:
##### moving average smoothing with different windows
palm_7_days_ave = palm_analysis[["date", 'mean_price']].set_index("date").rolling(7).mean()
palm_14_days_ave = palm_analysis[["date", 'mean_price']].set_index("date").rolling(14).mean()
palm_30_days_ave = palm_analysis[["date", 'mean_price']].set_index("date").rolling(30).mean()
palm_60_days_ave = palm_analysis[["date", 'mean_price']].set_index("date").rolling(60).mean()



In [109]:
fig = make_subplots(rows=3, cols=1,
                    specs=[[{"secondary_y": False}]
                           , [{"secondary_y": False}]
                           , [{"secondary_y": True}]
                           ])

fig.add_trace( go.Ohlc(x=palm_analysis["date"], open=palm_analysis["open"], high=palm_analysis["high"], 
                       low=palm_analysis["low"], close=palm_analysis["close"], name="OHLC plot" )
                , row=1 , col=1 )

fig.add_trace( go.Scatter( x=palm_analysis["date"], y=palm_analysis["mean_price"], name="daily meanprice"), row=2, col=1)
fig.add_trace( go.Scatter( x=palm_7_days_ave.index, y=palm_7_days_ave["mean_price"], name="7-day ave"), row=2, col=1)
fig.add_trace( go.Scatter( x=palm_14_days_ave.index, y=palm_14_days_ave["mean_price"], name="14-day ave"), row=2, col=1)
fig.add_trace( go.Scatter( x=palm_30_days_ave.index, y=palm_30_days_ave["mean_price"], name="30-day ave"), row=2, col=1)
fig.add_trace( go.Scatter( x=palm_14_days_ave.index, y=palm_60_days_ave["mean_price"], name="60-day ave"), row=2, col=1)

fig.add_trace( go.Scatter( x=palm_analysis["date"], y=palm_analysis["mean_price"], name="mean_price"), row=3, col=1)
fig.add_trace( go.Scatter( x=palm_analysis["date"], y=palm_analysis["high-low"], name="high - low"), row=3, col=1, secondary_y=True)
fig.add_trace( go.Scatter( x=palm_analysis["date"], y=palm_analysis["open-close"], name="open - close"), row=3, col=1, secondary_y=True)



fig.update_xaxes(title_text="Dates", row=1, col=1)
fig.update_yaxes(title_text="Price (MYR)", row=1, col=1)

fig.update_layout(xaxis_rangeslider_visible=False, height=750)
fig.show()

In [70]:
##### Decomposition 

palm_stl_decomp_7 = STL(palm_analysis['mean_price'], period=7).fit()
palm_stl_decomp_7 = pd.DataFrame(list(zip(palm_analysis["date"].to_list(),
                                          palm_analysis["mean_price"].to_list(),
                                          palm_stl_decomp_7.trend, 
                                          palm_stl_decomp_7.seasonal,
                                          palm_stl_decomp_7.resid,))
                                , columns=["date", "mean_price", "trend", "seasonal", "residual"])

palm_stl_decomp_30 = STL(palm_analysis['mean_price'], period=30).fit()
palm_stl_decomp_30 = pd.DataFrame(list(zip(palm_analysis["date"].to_list(),
                                          palm_analysis["mean_price"].to_list(),
                                          palm_stl_decomp_30.trend, 
                                          palm_stl_decomp_30.seasonal,
                                          palm_stl_decomp_30.resid,))
                                , columns=["date", "mean_price", "trend", "seasonal", "residual"])


In [71]:
fig = make_subplots(rows=4, cols=1)

fig.add_trace( go.Scatter(x=palm_stl_decomp_7["date"], y=palm_stl_decomp_7["mean_price"], name="mean_price"), row=1, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_7["date"], y=palm_stl_decomp_7["trend"], name="7-day trend"), row=2, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_7["date"], y=palm_stl_decomp_7["seasonal"], name="7-day seasonal"), row=3, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_7["date"], y=palm_stl_decomp_7["residual"], name="7-day residual"), row=4, col=1)

# fig.add_trace( go.Scatter(x=palm_stl_decomp_30["date"], y=palm_stl_decomp_30["mean_price"], name="mean_price"), row=1, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_30["date"], y=palm_stl_decomp_30["trend"], name="30-day trend"), row=2, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_30["date"], y=palm_stl_decomp_30["seasonal"], name="30-day seasonal"), row=3, col=1)
fig.add_trace( go.Scatter(x=palm_stl_decomp_30["date"], y=palm_stl_decomp_30["residual"], name="30-day residual"), row=4, col=1)


fig.update_layout(height=700)
fig.show()

In [113]:
temp = palm_analysis["mean_price"].to_frame()
temp["dummy_ind"] = temp.index
temp

mean_price  dummy_ind
0        2292.50          0
1        2292.50          1
2        2292.50          2
3        2303.50          3
4        2316.75          4
...          ...        ...
3279     3660.25       3279
3280     3689.25       3280
3281     3703.00       3281
3282     3673.25       3282
3283     3652.50       3283

[3284 rows x 2 columns]

In [60]:
palm_stl_decomp.seasonal

0      -11.043731
1      -13.667835
2      -14.975806
3       -8.906662
4        3.374889
          ...    
3279     3.606881
3280    29.212866
3281    36.482879
3282     9.156225
3283   -20.113305
Name: season, Length: 3284, dtype: float64

---
---

# <center> Model Building </center>

---

In [72]:
def rnn_prep(data, ndays, train_portion=0.7, n_outputs=1):

    data_len = len(data)-ndays if n_outputs==1 else len(data)-ndays-n_outputs

    ##### convert time-series to regression like problem
    x = []
    y = []


    for ii in range(data_len):
        x.append(data[ii:ii+ndays])

        if n_outputs == 1:
            y.append(data[ii+ndays])
        
        else:
            y.append(data[ii+ndays:ii+ndays+n_outputs])

    x = np.array(x)
    # x = x.reshape(x.shape[0], 1, x.shape[1])
    
    y = np.array(y)
    

    ##### split data
    
    # train_max_index = int(train_portion*npoints)
    train_max_index = int(train_portion*data_len)
    
    x_train = x[:train_max_index]
    y_train = y[:train_max_index]

    x_test = x[train_max_index:]
    y_test = y[train_max_index:]


    return x_train, y_train, x_test, y_test

        

    


In [99]:
input_days = 90
output_days = 14

x_train, y_train, x_test, y_test = rnn_prep(data=palm["open"], ndays=input_days, n_outputs=output_days)

x_scaler = MinMaxScaler()
x_scaler.fit(x_train)

y_scaler = MinMaxScaler()
# y_train = y_train.reshape(-1,1)
y_scaler.fit(y_train)

x_train = x_scaler.transform(x_train)
y_train = y_scaler.transform(y_train)

x_test = x_scaler.transform(x_test)
# y_test = y_test.reshape(-1,1)
y_test = y_scaler.transform(y_test)

#### Final reshape
x_train = x_train.reshape(x_train.shape[0], x_train.shape[1], 1)
x_test = x_test.reshape(x_test.shape[0], x_test.shape[1], 1)


In [114]:
x_train

array([[[0.22824156],
        [0.22824156],
        [0.22824156],
        ...,
        [0.14760687],
        [0.13477184],
        [0.13830916]],

       [[0.22824156],
        [0.22824156],
        [0.24511545],
        ...,
        [0.13920351],
        [0.13830916],
        [0.14255394]],

       [[0.22824156],
        [0.24511545],
        [0.2526643 ],
        ...,
        [0.14285714],
        [0.14255394],
        [0.16236293]],

       ...,

       [[0.94982238],
        [0.90097691],
        [0.86944938],
        ...,
        [0.99378882],
        [0.96215069],
        [0.96215069]],

       [[0.90097691],
        [0.86944938],
        [0.93605684],
        ...,
        [0.99378882],
        [0.96215069],
        [1.        ]],

       [[0.86944938],
        [0.93605684],
        [0.93605684],
        ...,
        [0.99378882],
        [1.        ],
        [0.98231341]]])

In [100]:
##### model building

model = Sequential()
model.add( LSTM(200, activation="relu", input_shape=(x_train.shape[1], 1)) )
model.add(RepeatVector(output_days) )
model.add( LSTM(200, activation="relu", return_sequences=True) )
model.add( TimeDistributed( Dense(100, activation="relu")))
model.add( TimeDistributed( Dense(1)) )
# model.add(LSTM(100, activation="relu"
#                # , input_shape=(x_train.shape[1], 1)
#                )
#             )
# model.add(Dense(output_days))

model.compile(optimizer="adam", loss="mae")
model.fit(x_train, y_train, epochs=500,
          callbacks=EarlyStopping(monitor="loss", patience=7, min_delta=0))

model.summary()


Epoch 1/500
70/70 [==============================] - 4s 48ms/step - loss: 0.0652
Epoch 2/500
70/70 [==============================] - 3s 47ms/step - loss: 0.0319
Epoch 3/500
70/70 [==============================] - 3s 47ms/step - loss: 0.0270
Epoch 4/500
70/70 [==============================] - 3s 47ms/step - loss: 0.0257
Epoch 5/500
70/70 [==============================] - 3s 48ms/step - loss: 0.0253
Epoch 6/500
70/70 [==============================] - 3s 49ms/step - loss: 0.0253
Epoch 7/500
70/70 [==============================] - 3s 47ms/step - loss: 0.0256
Epoch 8/500
70/70 [==============================] - 3s 48ms/step - loss: 0.0245
Epoch 9/500
70/70 [==============================] - 4s 52ms/step - loss: 0.0251
Epoch 10/500
70/70 [==============================] - 4s 51ms/step - loss: 0.0255
Epoch 11/500
70/70 [==============================] - 4s 55ms/step - loss: 0.0244
Epoch 12/500
70/70 [==============================] - 3s 48ms/step - loss: 0.0257
Epoch 13/500
70/70 [=====

In [101]:
##### Inverse Transform
# y_test = y_test
# y_test = y_scaler.inverse_transform(y_test)

prediction =  model.predict(x_test)
prediction = y_scaler.inverse_transform(prediction.reshape(prediction.shape[0],14))
prediction

palm_prediction = palm.loc[len(palm)-len(prediction):, ["date", "open"]].reset_index(drop=True)
palm_prediction

dates = []
values = []

for ii in range(len(palm_prediction)):
    for jj in range(len(prediction[0])):

        dates.append(palm_prediction.loc[ii, "date"] + pd.Timedelta(days=jj))
        values.append(prediction[ii][jj])

forecasts = pd.DataFrame(list(zip(dates, values)), columns=["date", "prediction"])
forecasts = forecasts.sort_values("date")
forecasts = forecasts.groupby(["date"]).mean().reset_index()
forecasts

palm_prediction["prediction"] = forecasts["prediction"]
# palm_prediction["prediction"] = prediction
palm_prediction

30/30 [==============================] - 1s 16ms/step


date    open   prediction
0   2021-05-20  4591.0  4630.700195
1   2021-05-21  4408.0  4648.760742
2   2021-05-22  4408.0  4727.991211
3   2021-05-23  4408.0  4756.033691
4   2021-05-24  4330.0  4773.134766
..         ...     ...          ...
949 2023-12-25  3655.0  3701.736572
950 2023-12-26  3683.0  3692.084717
951 2023-12-27  3700.0  3681.502441
952 2023-12-28  3685.0  3669.248535
953 2023-12-29  3663.0  3657.312988

[954 rows x 3 columns]

In [102]:
##### for record
# in7out7 = palm_prediction.copy(deep=True)
# in30out7 = palm_prediction.copy(deep=True)
# in60out7 = palm_prediction.copy(deep=True)
# in90out7 = palm_prediction.copy(deep=True)
# in90out30 = palm_prediction.copy(deep=True)
in90out14 = palm_prediction.copy(deep=True)





# in30out7_500epoch_coder

In [103]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Scatter(x=palm_prediction["date"], y=palm_prediction["open"], name="actual data"))
# fig.add_trace( go.Scatter(x=palm_prediction["date"], y=palm_prediction["prediction"]))
fig.add_trace( go.Scatter(x=in7out7["date"], y=in7out7["prediction"], name="7-day window"))
fig.add_trace( go.Scatter(x=in30out7["date"], y=in30out7["prediction"], name="30-day window"))
fig.add_trace( go.Scatter(x=in60out7["date"], y=in60out7["prediction"], name="60-day window"))
fig.add_trace( go.Scatter(x=in90out7["date"], y=in90out7["prediction"], name="90-day window"))
fig.add_trace( go.Scatter(x=in90out14["date"], y=in90out14["prediction"], name="90-day window 2"))
fig.add_trace( go.Scatter(x=in90out30["date"], y=in90out30["prediction"], name="90-day window 3"))


# fig.add_trace( go.Scatter(x=in30out14["date"], y=in30out14["prediction"], name="14 days prediction"))
# fig.add_trace( go.Scatter(x=in30out7["date"], y=in30out7["prediction"], name="7 days prediction"))
# fig.add_trace( go.Scatter(x=in30out7_500epoch["date"], y=in30out7_500epoch["prediction"], name="7 days prediction"))
# fig.add_trace( go.Scatter(x=in30out7_500epoch_200u["date"], y=in30out7_500epoch_200u["prediction"], name="7 days prediction -- 200 unit"))
# fig.add_trace( go.Scatter(x=in30out7_500epoch_coder["date"], y=in30out7_500epoch_coder["prediction"], name="7 days prediction -- coder"))



fig.update_layout(legend=dict(orientation="h"))
fig.show()

-----
# <center> Miscellaneous </center>

----

In [25]:
##### Make copy of palm data
palm_analysis = palm.copy(deep=True)
palm_analysis.head(5)

palm_diff = palm_analysis.drop(columns=["days", "no_business"]).diff(1)
palm_diff

date   close    open    high     low    vol.  change %      days  \
0 2015-01-02  2315.0  2265.0  2325.0  2265.0  1600.0      1.05    Friday   
1 2015-01-03  2315.0  2265.0  2325.0  2265.0  1600.0      1.05  Saturday   
2 2015-01-04  2315.0  2265.0  2325.0  2265.0  1600.0      1.05    Sunday   
3 2015-01-05  2298.0  2303.0  2320.0  2293.0   270.0     -0.73    Monday   
4 2015-01-06  2309.0  2320.0  2333.0  2305.0   590.0      0.48   Tuesday   

   no_business  
0        False  
1         True  
2         True  
3        False  
4        False

In [27]:
palm_diff = palm_analysis.drop(columns=["days", "no_business"]).diff(1)
palm_diff

date  close  open  high   low    vol.  change %
0       NaT    NaN   NaN   NaN   NaN     NaN       NaN
1    1 days    0.0   0.0   0.0   0.0     0.0      0.00
2    1 days    0.0   0.0   0.0   0.0     0.0      0.00
3    1 days  -17.0  38.0  -5.0  28.0 -1330.0     -1.78
4    1 days   11.0  17.0  13.0  12.0   320.0      1.21
...     ...    ...   ...   ...   ...     ...       ...
3279 1 days    0.0   0.0   0.0   0.0     0.0      0.00
3280 1 days   22.0  28.0  21.0  45.0   -20.0      0.52
3281 1 days    1.0  17.0  22.0  15.0   370.0     -0.57
3282 1 days  -43.0 -15.0 -27.0 -34.0   310.0     -1.19
3283 1 days    5.0 -22.0 -20.0 -46.0  -620.0      1.30

[3284 rows x 7 columns]

In [3]:
##### new columns
palm["open-close"] = palm["open"] - palm["close"]
palm["high-low"] = palm["high"] - palm["low"]
palm["oc_hl_ratio"] = palm["open-close"]/palm["high-low"]
palm["adj_oc_hl_ratio"] = palm["open-close"]/(palm["high-low"] + uniform(low=0, high=1/10000, size=len(palm["high-low"])))


palm

date   close    open    high     low    vol.  change %       days  \
0    2015-01-02  2315.0  2265.0  2325.0  2265.0  1600.0      1.05     Friday   
1    2015-01-03  2315.0  2265.0  2325.0  2265.0  1600.0      1.05   Saturday   
2    2015-01-04  2315.0  2265.0  2325.0  2265.0  1600.0      1.05     Sunday   
3    2015-01-05  2298.0  2303.0  2320.0  2293.0   270.0     -0.73     Monday   
4    2015-01-06  2309.0  2320.0  2333.0  2305.0   590.0      0.48    Tuesday   
...         ...     ...     ...     ...     ...     ...       ...        ...   
3279 2023-12-25  3677.0  3655.0  3679.0  3630.0   900.0      0.08     Monday   
3280 2023-12-26  3699.0  3683.0  3700.0  3675.0   880.0      0.60    Tuesday   
3281 2023-12-27  3700.0  3700.0  3722.0  3690.0  1250.0      0.03  Wednesday   
3282 2023-12-28  3657.0  3685.0  3695.0  3656.0  1560.0     -1.16   Thursday   
3283 2023-12-29  3662.0  3663.0  3675.0  3610.0   940.0      0.14     Friday   

      no_business  open-close  high-low  oc_hl_ratio  adj_oc_hl_ratio  
0           False       -50.0      60.0    -0.833333        -0.833333  
1            True       -50.0      60.0    -0.833333        -0.833333  
2            True       -50.0      60.0    -0.833333        -0.833333  
3           False         5.0      27.0     0.185185         0.185185  
4           False        11.0      28.0     0.392857         0.392857  
...           ...         ...       ...          ...              ...  
3279         True       -22.0      49.0    -0.448980        -0.448979  
3280        False       -16.0      25.0    -0.640000        -0.639999  
3281        False         0.0      32.0     0.000000         0.000000  
3282        False        28.0      39.0     0.717949         0.717948  
3283        False         1.0      65.0     0.015385         0.015385  

[3284 rows x 13 columns]

In [46]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Ohlc(x=palm["date"],
                              open=palm["open"], high=palm["high"], 
                              low=palm["low"], close=palm["close"]
                              ))

fig.update_layout(xaxis_rangeslider_visible=False)
fig.show()

In [24]:
nlags = 400

acf_data = pd.DataFrame([val for val in range(nlags+1)], columns=["lags"])
acf_data["close_acf"] = acf(palm["close"], nlags=nlags)
acf_data["open_acf"] = acf(palm["open"], nlags=nlags)
acf_data["high_acf"] = acf(palm["high"], nlags=nlags)
acf_data["low_acf"] = acf(palm["low"], nlags=nlags)
acf_data["vol_acf"] = acf(palm["vol."], nlags=nlags)







# acf_data

In [30]:
palm_diff.max()

date        1 days 00:00:00
close                 733.0
open                  835.0
high                  700.0
low                   662.0
vol.                 2840.0
change %              16.12
dtype: object

In [34]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["close_acf"]), row=1, col=1)
fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["open_acf"]), row=1, col=1)
fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["high_acf"]), row=1, col=1)
fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["low_acf"]), row=1, col=1)
# fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["vol_acf"]))

# fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["open_close_acf"]), row=2, col=1)
# fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["high_low_acf"]), row=2, col=1)
# fig.add_trace(go.Scatter( x=acf_data["lags"], y=acf_data["adj_oc_hl_acf"]), row=2, col=1)

fig.add_trace(go.Scatter( x=palm_analysis.loc[-1:, "date"], y=palm_diff["close"]), row=2, col=1)
fig.add_trace(go.Scatter( x=palm_analysis.loc[-1:,"date"], y=palm_diff["open"]), row=2, col=1)
fig.add_trace(go.Scatter( x=palm_analysis.loc[-1:,"date"], y=palm_diff["high"]), row=2, col=1)
fig.add_trace(go.Scatter( x=palm_analysis.loc[-1:,"date"], y=palm_diff["low"]), row=2, col=1)




fig.show()

In [33]:
palm_analysis.loc[-1:,"date"]

0      2015-01-02
1      2015-01-03
2      2015-01-04
3      2015-01-05
4      2015-01-06
          ...    
3279   2023-12-25
3280   2023-12-26
3281   2023-12-27
3282   2023-12-28
3283   2023-12-29
Name: date, Length: 3284, dtype: datetime64[ns]

In [82]:
palm.isna().any()

date           False
close          False
open           False
high           False
low            False
vol.           False
change %       False
days           False
no_business    False
open-close     False
high-low       False
oc_hl_ratio     True
dtype: bool

In [93]:
palm[palm["oc_hl_ratio"].isna()]

date   close    open    high     low   vol.  change %       days  \
7    2015-01-09  2359.0  2359.0  2359.0  2359.0  170.0     -1.05     Friday   
8    2015-01-10  2359.0  2359.0  2359.0  2359.0  170.0     -1.05   Saturday   
9    2015-01-11  2359.0  2359.0  2359.0  2359.0  170.0     -1.05     Sunday   
12   2015-01-14  2361.0  2361.0  2361.0  2361.0   30.0     -0.59  Wednesday   
13   2015-01-15  2373.0  2373.0  2373.0  2373.0   30.0      0.51   Thursday   
...         ...     ...     ...     ...     ...    ...       ...        ...   
3180 2023-09-17  3690.0  3690.0  3690.0  3690.0  150.0      0.82     Sunday   
3239 2023-11-15  3800.0  3800.0  3800.0  3800.0   10.0      1.09  Wednesday   
3269 2023-12-15  3601.0  3601.0  3601.0  3601.0   30.0      0.00     Friday   
3270 2023-12-16  3601.0  3601.0  3601.0  3601.0   30.0      0.00   Saturday   
3271 2023-12-17  3601.0  3601.0  3601.0  3601.0   30.0      0.00     Sunday   

      no_business  open-close  high-low  oc_hl_ratio  adj_oc_hl_ratio  
7           False         0.0       0.0          NaN              0.0  
8            True         0.0       0.0          NaN              0.0  
9            True         0.0       0.0          NaN              0.0  
12          False         0.0       0.0          NaN              0.0  
13          False         0.0       0.0          NaN              0.0  
...           ...         ...       ...          ...              ...  
3180         True         0.0       0.0          NaN              0.0  
3239        False         0.0       0.0          NaN              0.0  
3269        False         0.0       0.0          NaN              0.0  
3270         True         0.0       0.0          NaN              0.0  
3271         True         0.0       0.0          NaN              0.0  

[295 rows x 13 columns]

In [ ]:
nun